In [1]:
from ase_interface import ANIENS
from ase_interface import ensemblemolecule

import hdnntools as hdt

import numpy as np
import  ase
#from ase.build import molecule
#from ase.neb import NEB
#from ase.calculators.mopac import MOPAC
from ase.md.langevin import Langevin
from ase.md.verlet import VelocityVerlet
from ase.io.trajectory import Trajectory
from ase import units

from ase.md.velocitydistribution import MaxwellBoltzmannDistribution

from ase.optimize.fire import FIRE as QuasiNewton

from ase.md.nvtberendsen import NVTBerendsen
from ase.md import MDLogger

#from ase.neb import NEBtools
from ase.io import read, write
from ase.optimize import BFGS, LBFGS

import time

van Der Waals correction will be unavailable. Please install ased3


In [2]:
dir = '/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1/train_models/data-U0.001/testset/'

# Molecule file
molfile = '/nh/nest/u/jsmith/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1/test_files/data-U0.001/ts0/sys-000.xyz'

# Dynamics file
xyzfile = dir + 'mdcrd.xyz'

# Trajectory file
trajfile = dir + 'traj.dat'

# Optimized structure out:
optfile = dir + 'optmol.xyz'

ntdir = '/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1/train_models/data-U0.001/testsets/testset0'

T = 100.0 # Temperature
dt = 0.1
C = 2.0 # Optimization convergence
steps = 40000

ntdir = '/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1/train_models/data-U0.001/'
cns = ntdir + '../../params/rX-2.5R_32-2.0A_a8-8.params'
sae = ntdir + '../../params/sae.dat'
nnf = ntdir + 'train'
Nn = 1

#ntdir = '/nh/nest/u/jsmith/Research/gutzwiller_research/DarwinSets/GutzTrain/train_test_U2/U2_co3/'
#cns = ntdir + 'rX-6.0A_32-4.0A_a8-8.params'
#sae = ntdir + 'sae.dat'
#nnf = ntdir + 'train'
#Nn = 5

In [3]:
# Load molecule
mol = read(molfile)
L = 10.9753
mol.set_cell(([[L, 0, 0],
               [0, L, 0],
               [0, 0, L]]))

mol.set_pbc((True, True, True))

In [4]:
# Set NC
aens = ensemblemolecule(cns, sae, nnf, Nn, 1)

# Set ANI calculator
mol.set_calculator(ANIENS(aens, energy_conversion=12.0))

In [5]:
def erg_exp (Rmag):
    return 100.0*np.exp(-3.53*Rmag)

def frc_exp (Rmag,R):
    F = -3.53*erg_exp(Rmag)*(R/Rmag)                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
    return F

mol.calc.set_pairwise(erg_exp, frc_exp)

In [6]:
# Optimize molecule
start_time = time.time()
dyn = QuasiNewton(mol)
dyn.run(fmax=C)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

# Save optimized mol
spc = mol.get_chemical_symbols()
pos = mol.get_positions(wrap=False).reshape(1,len(spc),3)

hdt.writexyzfile(optfile, pos, spc)

      Step     Time          Energy         fmax
FIRE:    0 09:12:33     6762.536618      371.0882
FIRE:    1 09:12:33     6212.244011      310.7928
FIRE:    2 09:12:33     5722.528982      261.8221
FIRE:    3 09:12:33     5286.248814      221.8069
FIRE:    4 09:12:33     4897.268125      188.9212
FIRE:    5 09:12:33     4550.277577      161.7478
FIRE:    6 09:12:33     4240.670769      139.1800
FIRE:    7 09:12:33     3964.438861      120.3476
FIRE:    8 09:12:33     3718.038858      104.5774
FIRE:    9 09:12:33     3498.317512       91.3212
FIRE:   10 09:12:33     3302.478578       80.1372
FIRE:   11 09:12:33     3128.077924       70.6687
FIRE:   12 09:12:33     2972.873940       62.8092
FIRE:   13 09:12:33     2834.701781       59.3594
FIRE:   14 09:12:33     3005.188874       50.4328
FIRE:   15 09:12:33     2913.920737       47.0579
FIRE:   16 09:12:33     2832.710616       43.5715
FIRE:   17 09:12:33     2758.148078       48.9612
FIRE:   18 09:12:33     2684.502784       60.9853
F

In [7]:
MaxwellBoltzmannDistribution(mol, 10000.0 * units.kB)

# We want to run MD with constant energy using the VelocityVerlet algorithm.
dyn = VelocityVerlet(mol, dt * units.fs)

In [8]:
# Open MD output
mdcrd = open(xyzfile,'w')

# Open MD output
traj = open(trajfile,'w')

# Define the printer
def storeenergy(a=mol, d=dyn, b=mdcrd, t=traj):  # store a reference to atoms in the definition.
    """Function to print the potential, kinetic and total energy."""
    epot = a.get_potential_energy() / len(a)
    ekin = a.get_kinetic_energy() / len(a)

    stddev =  a.calc.stddev

    t.write(str(d.get_number_of_steps()) + ' ' + str(ekin / (1.5 * units.kB)) + ' ' + str(epot) + ' ' + str(ekin) + ' ' + str(epot+ekin) + '\n')
    b.write(str(len(a)) + '\n' + str(ekin / (1.5 * units.kB)) + ' Step: ' + str(d.get_number_of_steps()) + '\n')
    c = a.get_positions(wrap=True)
    for j, i in zip(a, c):
        b.write(str('C') + ' ' + str(i[0]) + ' ' + str(i[1]) + ' ' + str(i[2]) + '\n')

    print('Step: %d Energy per atom: Epot = %.3f  Ekin = %.3f (T=%.3fK)  '
          'Etot = %.6f' ' StdDev = %.3f' % (d.get_number_of_steps(), epot, ekin, ekin / (1.5 * units.kB), epot + ekin, stddev))
dyn.attach(storeenergy, interval=1)

In [9]:
start_time = time.time()
dyn.run(1000000)
print('[ANI Total time:', time.time() - start_time, 'seconds]')


Step: 1 Energy per atom: Epot = 5.634  Ekin = 1.354 (T=10477.900K)  Etot = 6.988869 StdDev = 0.000
Step: 2 Energy per atom: Epot = 5.648  Ekin = 1.341 (T=10374.269K)  Etot = 6.988919 StdDev = 0.000
Step: 3 Energy per atom: Epot = 5.670  Ekin = 1.319 (T=10203.081K)  Etot = 6.989012 StdDev = 0.000
Step: 4 Energy per atom: Epot = 5.701  Ekin = 1.288 (T=9966.551K)  Etot = 6.989145 StdDev = 0.000
Step: 5 Energy per atom: Epot = 5.740  Ekin = 1.250 (T=9668.749K)  Etot = 6.989317 StdDev = 0.000
Step: 6 Energy per atom: Epot = 5.785  Ekin = 1.204 (T=9315.572K)  Etot = 6.989525 StdDev = 0.000
Step: 7 Energy per atom: Epot = 5.837  Ekin = 1.152 (T=8914.484K)  Etot = 6.989761 StdDev = 0.000
Step: 8 Energy per atom: Epot = 5.895  Ekin = 1.095 (T=8474.080K)  Etot = 6.990020 StdDev = 0.000
Step: 9 Energy per atom: Epot = 5.956  Ekin = 1.035 (T=8003.902K)  Etot = 6.990301 StdDev = 0.000
Step: 10 Energy per atom: Epot = 6.019  Ekin = 0.971 (T=7514.612K)  Etot = 6.990605 StdDev = 0.000
Step: 11 Energy 

Step: 84 Energy per atom: Epot = 6.289  Ekin = 0.705 (T=5450.567K)  Etot = 6.993119 StdDev = 0.000
Step: 85 Energy per atom: Epot = 6.286  Ekin = 0.707 (T=5467.226K)  Etot = 6.993112 StdDev = 0.000
Step: 86 Energy per atom: Epot = 6.284  Ekin = 0.709 (T=5487.307K)  Etot = 6.993099 StdDev = 0.000
Step: 87 Energy per atom: Epot = 6.281  Ekin = 0.712 (T=5510.168K)  Etot = 6.993081 StdDev = 0.000
Step: 88 Energy per atom: Epot = 6.278  Ekin = 0.715 (T=5535.031K)  Etot = 6.993061 StdDev = 0.000
Step: 89 Energy per atom: Epot = 6.274  Ekin = 0.719 (T=5561.261K)  Etot = 6.993043 StdDev = 0.000
Step: 90 Energy per atom: Epot = 6.271  Ekin = 0.722 (T=5588.616K)  Etot = 6.993028 StdDev = 0.000
Step: 91 Energy per atom: Epot = 6.267  Ekin = 0.726 (T=5617.194K)  Etot = 6.993010 StdDev = 0.000
Step: 92 Energy per atom: Epot = 6.263  Ekin = 0.730 (T=5647.007K)  Etot = 6.992988 StdDev = 0.000
Step: 93 Energy per atom: Epot = 6.259  Ekin = 0.734 (T=5677.572K)  Etot = 6.992957 StdDev = 0.000
Step: 94 E

Step: 170 Energy per atom: Epot = 6.284  Ekin = 0.709 (T=5484.844K)  Etot = 6.993075 StdDev = 0.000
Step: 171 Energy per atom: Epot = 6.281  Ekin = 0.712 (T=5507.530K)  Etot = 6.993075 StdDev = 0.000
Step: 172 Energy per atom: Epot = 6.277  Ekin = 0.716 (T=5537.045K)  Etot = 6.993068 StdDev = 0.000
Step: 173 Energy per atom: Epot = 6.273  Ekin = 0.720 (T=5572.515K)  Etot = 6.993058 StdDev = 0.000
Step: 174 Energy per atom: Epot = 6.267  Ekin = 0.726 (T=5613.124K)  Etot = 6.993044 StdDev = 0.000
Step: 175 Energy per atom: Epot = 6.262  Ekin = 0.731 (T=5658.099K)  Etot = 6.993027 StdDev = 0.000
Step: 176 Energy per atom: Epot = 6.255  Ekin = 0.738 (T=5706.605K)  Etot = 6.993005 StdDev = 0.000
Step: 177 Energy per atom: Epot = 6.249  Ekin = 0.744 (T=5757.611K)  Etot = 6.992980 StdDev = 0.000
Step: 178 Energy per atom: Epot = 6.242  Ekin = 0.751 (T=5809.738K)  Etot = 6.992950 StdDev = 0.000
Step: 179 Energy per atom: Epot = 6.235  Ekin = 0.758 (T=5861.253K)  Etot = 6.992917 StdDev = 0.000


Step: 254 Energy per atom: Epot = 6.249  Ekin = 0.743 (T=5747.949K)  Etot = 6.992065 StdDev = 0.000
Step: 255 Energy per atom: Epot = 6.245  Ekin = 0.747 (T=5782.248K)  Etot = 6.992048 StdDev = 0.000
Step: 256 Energy per atom: Epot = 6.240  Ekin = 0.752 (T=5816.553K)  Etot = 6.992033 StdDev = 0.000
Step: 257 Energy per atom: Epot = 6.236  Ekin = 0.756 (T=5850.818K)  Etot = 6.992020 StdDev = 0.000
Step: 258 Energy per atom: Epot = 6.231  Ekin = 0.761 (T=5885.020K)  Etot = 6.992010 StdDev = 0.000
Step: 259 Energy per atom: Epot = 6.227  Ekin = 0.765 (T=5919.087K)  Etot = 6.992001 StdDev = 0.000
Step: 260 Energy per atom: Epot = 6.223  Ekin = 0.769 (T=5952.842K)  Etot = 6.991995 StdDev = 0.000
Step: 261 Energy per atom: Epot = 6.218  Ekin = 0.774 (T=5986.013K)  Etot = 6.991990 StdDev = 0.000
Step: 262 Energy per atom: Epot = 6.214  Ekin = 0.778 (T=6018.223K)  Etot = 6.991990 StdDev = 0.000
Step: 263 Energy per atom: Epot = 6.210  Ekin = 0.782 (T=6049.006K)  Etot = 6.991996 StdDev = 0.000


Step: 337 Energy per atom: Epot = 6.247  Ekin = 0.746 (T=5770.968K)  Etot = 6.993066 StdDev = 0.000
Step: 338 Energy per atom: Epot = 6.251  Ekin = 0.743 (T=5744.769K)  Etot = 6.993088 StdDev = 0.000
Step: 339 Energy per atom: Epot = 6.254  Ekin = 0.739 (T=5714.791K)  Etot = 6.993105 StdDev = 0.000
Step: 340 Energy per atom: Epot = 6.259  Ekin = 0.734 (T=5681.806K)  Etot = 6.993118 StdDev = 0.000
Step: 341 Energy per atom: Epot = 6.263  Ekin = 0.730 (T=5646.492K)  Etot = 6.993127 StdDev = 0.000
Step: 342 Energy per atom: Epot = 6.268  Ekin = 0.725 (T=5609.500K)  Etot = 6.993132 StdDev = 0.000
Step: 343 Energy per atom: Epot = 6.273  Ekin = 0.720 (T=5571.542K)  Etot = 6.993135 StdDev = 0.000
Step: 344 Energy per atom: Epot = 6.278  Ekin = 0.715 (T=5533.458K)  Etot = 6.993135 StdDev = 0.000
Step: 345 Energy per atom: Epot = 6.283  Ekin = 0.710 (T=5496.231K)  Etot = 6.993130 StdDev = 0.000
Step: 346 Energy per atom: Epot = 6.287  Ekin = 0.706 (T=5460.920K)  Etot = 6.993122 StdDev = 0.000


...

Step: 45238 Energy per atom: Epot = 6.253  Ekin = 0.740 (T=5722.918K)  Etot = 6.993207 StdDev = 0.000
Step: 45239 Energy per atom: Epot = 6.264  Ekin = 0.729 (T=5640.427K)  Etot = 6.993236 StdDev = 0.000
Step: 45240 Energy per atom: Epot = 6.274  Ekin = 0.719 (T=5562.183K)  Etot = 6.993258 StdDev = 0.000
Step: 45241 Energy per atom: Epot = 6.284  Ekin = 0.710 (T=5490.371K)  Etot = 6.993271 StdDev = 0.000
Step: 45242 Energy per atom: Epot = 6.292  Ekin = 0.701 (T=5426.704K)  Etot = 6.993279 StdDev = 0.000
Step: 45243 Energy per atom: Epot = 6.299  Ekin = 0.694 (T=5372.454K)  Etot = 6.993281 StdDev = 0.000
Step: 45244 Energy per atom: Epot = 6.305  Ekin = 0.689 (T=5328.563K)  Etot = 6.993279 StdDev = 0.000
Step: 45245 Energy per atom: Epot = 6.309  Ekin = 0.685 (T=5295.754K)  Etot = 6.993273 StdDev = 0.000
Step: 45246 Energy per atom: Epot = 6.311  Ekin = 0.682 (T=5274.518K)  Etot = 6.993264 StdDev = 0.000
Step: 45247 Energy per atom: Epot = 6.313  Ekin = 0.681 (T=5265.012K)  Etot = 6.99

Step: 45322 Energy per atom: Epot = 6.243  Ekin = 0.750 (T=5798.846K)  Etot = 6.992785 StdDev = 0.000
Step: 45323 Energy per atom: Epot = 6.241  Ekin = 0.752 (T=5814.816K)  Etot = 6.992762 StdDev = 0.000
Step: 45324 Energy per atom: Epot = 6.239  Ekin = 0.754 (T=5830.388K)  Etot = 6.992737 StdDev = 0.000
Step: 45325 Energy per atom: Epot = 6.237  Ekin = 0.756 (T=5844.955K)  Etot = 6.992708 StdDev = 0.000
Step: 45326 Energy per atom: Epot = 6.235  Ekin = 0.757 (T=5857.858K)  Etot = 6.992678 StdDev = 0.000
Step: 45327 Energy per atom: Epot = 6.234  Ekin = 0.759 (T=5868.373K)  Etot = 6.992647 StdDev = 0.000
Step: 45328 Energy per atom: Epot = 6.233  Ekin = 0.760 (T=5875.786K)  Etot = 6.992620 StdDev = 0.000
Step: 45329 Energy per atom: Epot = 6.233  Ekin = 0.760 (T=5879.488K)  Etot = 6.992597 StdDev = 0.000
Step: 45330 Energy per atom: Epot = 6.233  Ekin = 0.760 (T=5879.102K)  Etot = 6.992580 StdDev = 0.000
Step: 45331 Energy per atom: Epot = 6.233  Ekin = 0.759 (T=5874.662K)  Etot = 6.99

Step: 45403 Energy per atom: Epot = 6.321  Ekin = 0.673 (T=5203.221K)  Etot = 6.993177 StdDev = 0.000
Step: 45404 Energy per atom: Epot = 6.324  Ekin = 0.669 (T=5179.241K)  Etot = 6.993162 StdDev = 0.000
Step: 45405 Energy per atom: Epot = 6.326  Ekin = 0.668 (T=5164.765K)  Etot = 6.993138 StdDev = 0.000
Step: 45406 Energy per atom: Epot = 6.326  Ekin = 0.667 (T=5160.542K)  Etot = 6.993106 StdDev = 0.000
Step: 45407 Energy per atom: Epot = 6.325  Ekin = 0.668 (T=5167.065K)  Etot = 6.993070 StdDev = 0.000
Step: 45408 Energy per atom: Epot = 6.323  Ekin = 0.670 (T=5184.660K)  Etot = 6.993030 StdDev = 0.000
Step: 45409 Energy per atom: Epot = 6.319  Ekin = 0.674 (T=5213.499K)  Etot = 6.992985 StdDev = 0.000
Step: 45410 Energy per atom: Epot = 6.314  Ekin = 0.679 (T=5253.434K)  Etot = 6.992934 StdDev = 0.000
Step: 45411 Energy per atom: Epot = 6.307  Ekin = 0.686 (T=5303.752K)  Etot = 6.992878 StdDev = 0.000
Step: 45412 Energy per atom: Epot = 6.300  Ekin = 0.693 (T=5363.019K)  Etot = 6.99

Step: 45488 Energy per atom: Epot = 6.266  Ekin = 0.727 (T=5625.931K)  Etot = 6.993640 StdDev = 0.000
Step: 45489 Energy per atom: Epot = 6.264  Ekin = 0.729 (T=5642.104K)  Etot = 6.993651 StdDev = 0.000
Step: 45490 Energy per atom: Epot = 6.263  Ekin = 0.731 (T=5653.802K)  Etot = 6.993671 StdDev = 0.000
Step: 45491 Energy per atom: Epot = 6.262  Ekin = 0.732 (T=5661.300K)  Etot = 6.993700 StdDev = 0.000
Step: 45492 Energy per atom: Epot = 6.261  Ekin = 0.732 (T=5665.458K)  Etot = 6.993736 StdDev = 0.000
Step: 45493 Energy per atom: Epot = 6.261  Ekin = 0.733 (T=5667.542K)  Etot = 6.993772 StdDev = 0.000
Step: 45494 Energy per atom: Epot = 6.261  Ekin = 0.733 (T=5668.841K)  Etot = 6.993803 StdDev = 0.000
Step: 45495 Energy per atom: Epot = 6.261  Ekin = 0.733 (T=5670.323K)  Etot = 6.993826 StdDev = 0.000
Step: 45496 Energy per atom: Epot = 6.261  Ekin = 0.733 (T=5672.477K)  Etot = 6.993842 StdDev = 0.000
Step: 45497 Energy per atom: Epot = 6.260  Ekin = 0.734 (T=5675.349K)  Etot = 6.99

KeyboardInterrupt: 